In [2]:
import pandas as pd
import numpy as np

import scipy.stats as ss
import statsmodels.api as sm
import statsmodels.formula.api as smf
from statsmodels.stats.api import anova_lm
from statsmodels.stats.multicomp import (pairwise_tukeyhsd,
                                         MultiComparison)
import pingouin as pg

import matplotlib.pyplot as plt
import seaborn as sns
from datetime import datetime, timedelta


%matplotlib inline
sns.set(
    font_scale =2,
    style      ="whitegrid",
    rc         ={'figure.figsize':(20,7)}
)

## Выполняем 1-ое задание:


In [3]:
# во первых извлечем нужные нам данные

# данные о времени захода пользователей в игру
df_auth = pd.read_csv("problem1-auth_data.csv", delimiter=";")
df_auth

C:\Users\Admin\anaconda3\lib\site-packages\outdated\utils.py:14: OutdatedPackageWarning: The package pingouin is out of date. Your version is 0.5.3, the latest is 0.5.4.
Set the environment variable OUTDATED_IGNORE=1 to disable these warnings.
  return warn(


auth_ts      uid
0         911382223        1
1         932683089        2
2         932921206        2
3         933393015        2
4         933875379        2
...             ...      ...
9601008  1600874034  1110618
9601009  1600874086  1110619
9601010  1600874139  1110620
9601011  1600874191  1110621
9601012  1600874244  1110622

[9601013 rows x 2 columns]

In [4]:
# данные о времени регистрации пользователей
df_reg = pd.read_csv("problem1-reg_data.csv", delimiter=";")
df_reg

reg_ts      uid
0        911382223        1
1        932683089        2
2        947802447        3
3        959523541        4
4        969103313        5
...            ...      ...
999995  1600874034  1110618
999996  1600874086  1110619
999997  1600874139  1110620
999998  1600874191  1110621
999999  1600874244  1110622

[1000000 rows x 2 columns]

In [9]:
# объединяем датафреймы в один
data = df_auth.merge(df_reg, how="left")
data

auth_ts      uid      reg_ts
0         911382223        1   911382223
1         932683089        2   932683089
2         932921206        2   932683089
3         933393015        2   932683089
4         933875379        2   932683089
...             ...      ...         ...
9601008  1600874034  1110618  1600874034
9601009  1600874086  1110619  1600874086
9601010  1600874139  1110620  1600874139
9601011  1600874191  1110621  1600874191
9601012  1600874244  1110622  1600874244

[9601013 rows x 3 columns]

In [10]:
# проверка на то, что мы ничего не потеряли
data.isna().sum()

auth_ts    0
uid        0
reg_ts     0
dtype: int64

In [11]:
data = data[["uid", "auth_ts", "reg_ts"]]

In [12]:
data["auth_ts"] = pd.to_datetime(data.auth_ts, unit="s")
data["reg_ts"] = pd.to_datetime(data.reg_ts, unit="s")


In [60]:
data

uid             auth_ts              reg_ts
0              1 1998-11-18 09:43:43 1998-11-18 09:43:43
1              2 1999-07-22 22:38:09 1999-07-22 22:38:09
2              2 1999-07-25 16:46:46 1999-07-22 22:38:09
3              2 1999-07-31 03:50:15 1999-07-22 22:38:09
4              2 1999-08-05 17:49:39 1999-07-22 22:38:09
...          ...                 ...                 ...
9601008  1110618 2020-09-23 15:13:54 2020-09-23 15:13:54
9601009  1110619 2020-09-23 15:14:46 2020-09-23 15:14:46
9601010  1110620 2020-09-23 15:15:39 2020-09-23 15:15:39
9601011  1110621 2020-09-23 15:16:31 2020-09-23 15:16:31
9601012  1110622 2020-09-23 15:17:24 2020-09-23 15:17:24

[9601013 rows x 3 columns]

In [29]:
# пишем функцию для определения показателя retention
def get_daily_retention(df_reg: pd.DataFrame, df_auth: pd.DataFrame):
    """
    Функция get_retention предназначена для подсчета ежедневного retention пользавателей
    
    :param df_reg: датафрейм c данными о времени регистрации (тип данных -> pd.DataDrame)
    :param df_auth:  датафрейм c данными о времени захода пользователей в игру (тип данных -> pd.DataDrame)
    
    : return retention
    """
    
    # объединяем датафремы
    data = df_auth.merge(df_reg, how="left", on="uid")
#     data = data[["uid", "auth_ts", "reg_ts"]]
    
    # переводим unix-t в дату
    data["auth_ts"] = pd.to_datetime(data.auth_ts, unit="s")
    data["reg_ts"] = pd.to_datetime(data.reg_ts, unit="s")
    
    # обрезаем даты до дней
    data["reg_ts"] =  pd.to_datetime(data.reg_ts.dt.date)
    data["auth_ts"] =  pd.to_datetime(data.auth_ts.dt.date)

    
    # Сформируем словарь с когортам, где значения словаря - уникальные пользователи этой кагорты
    cagorts_dict = {}
    for date in list(data.reg_ts.unique()):
        cagorts_dict[date] = list(data.query("reg_ts == @date").uid.unique())
    
    # найдем максимальную дату в датафрейме по колонке "auth_ts", это будет дата конца анализа
    end_of_retantion_date = data["auth_ts"].max().date()
    
    
    # Сформируем словарь ключей когорт, чтобы было легче итерироваться
    cagorts_dict_keys_list = list(cagorts_dict.keys())
    
    retention_df = pd.DataFrame() # создаем пустой датафрейм

    for cagort in cagorts_dict_keys_list:
        # пользователи текущей кагорты
        current_cagort_users = cagorts_dict[cagort]

        retention_list = [] # список retantion нужен для создания DataFrame

        for date in create_date_range(pd.to_datetime(cagort), end_of_retantion_date):

            # пользователи текущей или следующей кагорты
            next_cagort_users = list(data.query("auth_ts == @date").uid.unique())

            # подсчитываем retention через sets
            retention = len(set(current_cagort_users).intersection(set(next_cagort_users))) * 100 / len(current_cagort_users)

            #добавляем полученный retention в словарь
            retention_list.append(retention)

        # записываем данные в датафрейм
        row = pd.DataFrame(data=retention_list, columns=[pd.to_datetime(cagort)]) # делаем датафрейм-строку

        retention_df = pd.concat([retention_df, row], ignore_index=False, axis=1) # соединяем подсчеты

    retention_df = retention_df.transpose() # переворачиваем табличку

    
    # подкрасим значения
    styled_df = (retention_df
                .style
                .set_caption('User retention by cohort')
                .background_gradient(cmap='viridis')
                .highlight_null('white')
                .format("{:.2f}%",na_rep=""))
    
    return styled_df

In [62]:
get_retention(reg_data, auth_data)

TypeError: get_retention() missing 1 required positional argument: 'end_cagort_date'

In [63]:
data

uid             auth_ts              reg_ts
0              1 1998-11-18 09:43:43 1998-11-18 09:43:43
1              2 1999-07-22 22:38:09 1999-07-22 22:38:09
2              2 1999-07-25 16:46:46 1999-07-22 22:38:09
3              2 1999-07-31 03:50:15 1999-07-22 22:38:09
4              2 1999-08-05 17:49:39 1999-07-22 22:38:09
...          ...                 ...                 ...
9601008  1110618 2020-09-23 15:13:54 2020-09-23 15:13:54
9601009  1110619 2020-09-23 15:14:46 2020-09-23 15:14:46
9601010  1110620 2020-09-23 15:15:39 2020-09-23 15:15:39
9601011  1110621 2020-09-23 15:16:31 2020-09-23 15:16:31
9601012  1110622 2020-09-23 15:17:24 2020-09-23 15:17:24

[9601013 rows x 3 columns]

In [20]:
%%time
data = df_auth.merge(df_reg, how="left", on="uid")
data = data[["uid", "auth_ts", "reg_ts"]]

data["auth_ts"] = pd.to_datetime(data.auth_ts, unit="s")
data["reg_ts"] = pd.to_datetime(data.reg_ts, unit="s")
# обрезаем даты до дней
data["reg_ts"] =  pd.to_datetime(data.reg_ts.dt.date)
data["auth_ts"] =  pd.to_datetime(data.auth_ts.dt.date)

# уреже датасет для теста
data = data.query("auth_ts >= '18.11.1998' and auth_ts <= '18.11.2003'")



C:\Users\Admin\anaconda3\lib\site-packages\pandas\core\computation\expr.py:538: UserWarning: Parsing '18.11.1998' in DD/MM/YYYY format. Provide format or specify infer_datetime_format=True for consistent parsing.
  return self._maybe_evaluate_binop(op, op_class, left, right)
C:\Users\Admin\anaconda3\lib\site-packages\pandas\core\computation\expr.py:538: UserWarning: Parsing '18.11.2003' in DD/MM/YYYY format. Provide format or specify infer_datetime_format=True for consistent parsing.
  return self._maybe_evaluate_binop(op, op_class, left, right)


CPU times: total: 11.6 s
Wall time: 11.6 s


In [21]:
data

uid    auth_ts     reg_ts
0      1 1998-11-18 1998-11-18
1      2 1999-07-22 1999-07-22
2      2 1999-07-25 1999-07-22
3      2 1999-07-31 1999-07-22
4      2 1999-08-05 1999-07-22
..   ...        ...        ...
472    2 2003-11-04 1999-07-22
473    2 2003-11-11 1999-07-22
474    2 2003-11-13 1999-07-22
475   43 2003-11-14 2003-11-14
476    2 2003-11-17 1999-07-22

[477 rows x 3 columns]

In [22]:
len(data.reg_ts.unique())

39

In [23]:
%%time
# Формируем датафрэйм с когортами
cagorts_dict = {}
for date in list(data.reg_ts.unique()):
    cagorts_dict[date] = list(data.query("reg_ts == @date").uid.unique())


CPU times: total: 78.1 ms
Wall time: 78.7 ms


In [24]:
end_of_retantion_date = data["auth_ts"].max().date()
end_of_retantion_date

datetime.date(2003, 11, 17)

In [25]:
def create_date_range(start_date, end_date):
    date_range = []
    current_date = start_date

    while current_date <= end_date:
        date_range.append(current_date)
        current_date += timedelta(days=1)

    return date_range

In [26]:
len(create_date_range(data["auth_ts"].min().date(), data["auth_ts"].max().date()))

1826

In [27]:
# Сформируем словарь ключей когорт, чтобы было легче итерироваться
cagorts_dict_keys_list = list(cagorts_dict.keys())
cagorts_dict_keys_list

[numpy.datetime64('1998-11-18T00:00:00.000000000'),
 numpy.datetime64('1999-07-22T00:00:00.000000000'),
 numpy.datetime64('2000-01-13T00:00:00.000000000'),
 numpy.datetime64('2000-05-28T00:00:00.000000000'),
 numpy.datetime64('2000-09-16T00:00:00.000000000'),
 numpy.datetime64('2000-12-19T00:00:00.000000000'),
 numpy.datetime64('2001-03-10T00:00:00.000000000'),
 numpy.datetime64('2001-05-21T00:00:00.000000000'),
 numpy.datetime64('2001-07-24T00:00:00.000000000'),
 numpy.datetime64('2001-09-20T00:00:00.000000000'),
 numpy.datetime64('2001-11-12T00:00:00.000000000'),
 numpy.datetime64('2001-12-30T00:00:00.000000000'),
 numpy.datetime64('2002-02-13T00:00:00.000000000'),
 numpy.datetime64('2002-03-27T00:00:00.000000000'),
 numpy.datetime64('2002-05-05T00:00:00.000000000'),
 numpy.datetime64('2002-06-11T00:00:00.000000000'),
 numpy.datetime64('2002-07-16T00:00:00.000000000'),
 numpy.datetime64('2002-08-18T00:00:00.000000000'),
 numpy.datetime64('2002-09-18T00:00:00.000000000'),
 numpy.datet

In [28]:
%%time

retention_df = pd.DataFrame() # создаем пустой датафрейм

for cagort in cagorts_dict_keys_list:
    # пользователи текущей кагорты
    current_cagort_users = cagorts_dict[cagort]
    
    retention_list = [] # список retantion нужен для создания DataFrame
    
    for date in create_date_range(pd.to_datetime(cagort), end_of_retantion_date):

        # пользователи текущей или следующей кагорты
        next_cagort_users = list(data.query("auth_ts == @date").uid.unique())
        
        # подсчитываем retention через sets
        retention = len(set(current_cagort_users).intersection(set(next_cagort_users))) * 100 / len(current_cagort_users)
        
#         print(cagort, ": ", retention)
        #добавляем полученный retention в словарь
        retention_list.append(retention)

        # записываем данные в датафрейм
    row = pd.DataFrame(data=retention_list, columns=[pd.to_datetime(cagort)]) # делаем датафрейм-строку

    retention_df = pd.concat([retention_df, row], ignore_index=False, axis=1) # соединяем подсчеты

retention_df = retention_df.transpose() # переворачиваем табличку
styled_df = (retention_df
                .style
                .set_caption('User retention by cohort')
                .background_gradient(cmap='viridis')
                .highlight_null('white')
                .format("{:.2f}%",na_rep=""))
styled_df
        

C:\Users\Admin\AppData\Local\Temp\ipykernel_6508\2048179858.py:5: FutureWarning: Comparison of Timestamp with datetime.date is deprecated in order to match the standard library behavior. In a future version these will be considered non-comparable. Use 'ts == pd.Timestamp(date)' or 'ts.date() == date' instead.
  while current_date <= end_date:
C:\Users\Admin\AppData\Local\Temp\ipykernel_6508\2048179858.py:5: FutureWarning: Comparison of Timestamp with datetime.date is deprecated in order to match the standard library behavior. In a future version these will be considered non-comparable. Use 'ts == pd.Timestamp(date)' or 'ts.date() == date' instead.
  while current_date <= end_date:
C:\Users\Admin\AppData\Local\Temp\ipykernel_6508\2048179858.py:5: FutureWarning: Comparison of Timestamp with datetime.date is deprecated in order to match the standard library behavior. In a future version these will be considered non-comparable. Use 'ts == pd.Timestamp(date)' or 'ts.date() == date' instead.

C:\Users\Admin\AppData\Local\Temp\ipykernel_6508\2048179858.py:5: FutureWarning: Comparison of Timestamp with datetime.date is deprecated in order to match the standard library behavior. In a future version these will be considered non-comparable. Use 'ts == pd.Timestamp(date)' or 'ts.date() == date' instead.
  while current_date <= end_date:
C:\Users\Admin\AppData\Local\Temp\ipykernel_6508\2048179858.py:5: FutureWarning: Comparison of Timestamp with datetime.date is deprecated in order to match the standard library behavior. In a future version these will be considered non-comparable. Use 'ts == pd.Timestamp(date)' or 'ts.date() == date' instead.
  while current_date <= end_date:
C:\Users\Admin\AppData\Local\Temp\ipykernel_6508\2048179858.py:5: FutureWarning: Comparison of Timestamp with datetime.date is deprecated in order to match the standard library behavior. In a future version these will be considered non-comparable. Use 'ts == pd.Timestamp(date)' or 'ts.date() == date' instead.

CPU times: total: 29.3 s
Wall time: 29.3 s


# Задание 2

### Имеются результаты A/B теста, в котором двум группам пользователей предлагались различные наборы акционных предложений. Известно, что ARPU в тестовой группе выше на 5%, чем в контрольной. При этом в контрольной группе 1928 игроков из 202103 оказались платящими, а в тестовой – 1805 из 202667.

### Какой набор предложений можно считать лучшим? Какие метрики стоит проанализировать для принятия правильного решения и как?

In [98]:
data = pd.read_csv("problem2.csv", delimiter=";")
data

user_id  revenue testgroup
0             1        0         b
1             2        0         a
2             3        0         a
3             4        0         b
4             5        0         b
...         ...      ...       ...
404765   404766        0         a
404766   404767        0         b
404767   404768      231         a
404768   404769        0         a
404769   404770        0         b

[404770 rows x 3 columns]

In [71]:
convetion_data = (data.groupby("testgroup", as_index=False)
        .agg({"user_id": "count"})
        .rename(columns= {"user_id": "count_of_users"})
        )
convetion_data

testgroup  count_of_users
0         a          202103
1         b          202667

In [72]:
a_group_buying_users = data.query("testgroup == 'a' and revenue > 0").agg({"user_id": "count"})
a_group_buying_users

user_id    1928
dtype: int64

In [73]:
b_group_buying_users = data.query("testgroup == 'b' and revenue > 0").agg({"user_id": "count"})
b_group_buying_users

user_id    1805
dtype: int64

In [74]:
# Для принятия правильного решения о том,
# какой набор предложений лучше, можно проанализировать несколько метрик, таких как:
# Conversion Rate, ARPPU, Retention Rate и CLV.

In [75]:
# посмотрим на Conversion Rate
convetion_data["buyers_count"] = pd.Series([a_group_buying_users[0], b_group_buying_users[0]])
convetion_data

testgroup  count_of_users  buyers_count
0         a          202103          1928
1         b          202667          1805

In [77]:
convetion_data["convertion_rate"] = convetion_data["buyers_count"] / convetion_data["count_of_users"] * 100
convetion_data

testgroup  count_of_users  buyers_count  convertion_rate
0         a          202103          1928         0.953969
1         b          202667          1805         0.890624

In [80]:
# Считаем Average Revenue per Paying User (ARPPU) и ARPU
ARPU_ARPPU_data = convetion_data

In [81]:
# Считаем общий доход для двух групп
ARPU_ARPPU_data["total_revenue"] = (data.groupby("testgroup", as_index=False)
        .agg({"revenue": "sum"})
        .rename(columns= {"revenue": "total_revenue"})
        .total_revenue
        )
ARPU_ARPPU_data

testgroup  count_of_users  buyers_count  convertion_rate  total_revenue
0         a          202103          1928         0.953969        5136189
1         b          202667          1805         0.890624        5421603

In [83]:
# Считаем Average Revenue per Paying User (ARPPU) и ARPU
ARPU_ARPPU_data["ARPU"] = ARPU_ARPPU_data["total_revenue"] / ARPU_ARPPU_data["count_of_users"]
ARPU_ARPPU_data["ARPPU"] = ARPU_ARPPU_data["total_revenue"] / ARPU_ARPPU_data["buyers_count"]
ARPU_ARPPU_data

testgroup  count_of_users  buyers_count  convertion_rate  total_revenue  \
0         a          202103          1928         0.953969        5136189   
1         b          202667          1805         0.890624        5421603   

        ARPU        ARPPU  
0  25.413720  2663.998444  
1  26.751287  3003.658172

In [99]:
# Тестируем нормальность

print(ss.shapiro(data.query("testgroup == 'a'").revenue))
print(ss.shapiro(data.query("testgroup == 'b'").revenue))

# данные распределены ненормально


ShapiroResult(statistic=0.008876502513885498, pvalue=0.0)
ShapiroResult(statistic=0.06588172912597656, pvalue=0.0)


C:\Users\Admin\anaconda3\lib\site-packages\scipy\stats\morestats.py:1760: UserWarning: p-value may not be accurate for N > 5000.
  warnings.warn("p-value may not be accurate for N > 5000.")


In [100]:
# тестируем гомогенность дисперсий
ss.levene(data.query("testgroup == 'a'").revenue, data.query("testgroup == 'b'").revenue)

# дисперсии в двух группах одинаковы

LeveneResult(statistic=0.3896289474701388, pvalue=0.5324948591043842)

In [103]:
# соответственно следует применить непараметривческий U-тест
ss.mannwhitneyu(data.query("testgroup == 'a'").revenue, data.query("testgroup == 'b'").revenue)

MannwhitneyuResult(statistic=20491259376.0, pvalue=0.06269701316074398)

In [104]:
# Исходя из проведенного анализа выдвигаю несколько суждений о проделанной работе:

# 1. ARPU и ARPPU в тестовой группе больше, чем в контрольной:
#     Это положительный результат, который указывает на то,
#     что новый набор предложений, представленный в тестовой группе,
#     может способствовать увеличению доходов от пользователей.

# 2. Conversion Rate выше в контрольной группе: Это может свидетельствовать
#     о том, что контрольная группа показывает небольшое преимущество в
#     преобразовании пользователей в платящих. Несмотря на это, важно оценить,
#     насколько значимо это различие с точки зрения бизнеса.

# 3. Результаты U-критерия: Если U-критерий показал, что различия в доходах не являются
#     статистически значимыми при уровне значимости 0.05, это может означать, что даже
#     несмотря на небольшое преимущество в Conversion Rate у контрольной группы, доходы
#     в тестовой группе все равно остаются выше.

# 4. Интерпретация: Важно проанализировать, какие именно метрики более важны для бизнеса.
#     Если Conversion Rate важнее для вас, чем ARPU и ARPPU, то небольшое преимущество
#     в Conversion Rate в контрольной группе может быть значимым. Однако, если более
#     важными являются доходы, то увеличение ARPU и ARPPU в тестовой группе может
#     быть более значимым.

# 5. Дополнительные анализы: Рекомендуется провести дополнительные анализы и рассмотреть
#     другие факторы, которые могут повлиять на доходы пользователей (например,
#     Retention Rate, сегментация пользователей и т. д.), чтобы получить более
#     полное понимание результатов A/B-теста и принять обоснованное решение о внедрении изменений
#     (но к сожалению такого рода данные в этом задании не предлагались).

# Задание 3

### В игре Plants & Gardens каждый месяц проводятся тематические события, ограниченные по времени. В них игроки могут получить уникальные предметы для сада и персонажей, дополнительные монеты или бонусы. Для получения награды требуется пройти ряд уровней за определенное время. С помощью каких метрик можно оценить результаты последнего прошедшего события?

### Предположим, в другом событии мы усложнили механику событий так, что при каждой неудачной попытке выполнения уровня игрок будет откатываться на несколько уровней назад. Изменится ли набор метрик оценки результата? Если да, то как?


### Ответ на первый вопрос:

Для оценки результатов последнего прошедшего события в игре Plants & Gardens можно использовать следующие метрики:

* **Retention Rate**. Эта метрика позволяет оценить, насколько успешно
  событие удерживает игроков в игре после его завершения.
  С помощью нее мы можем проследить, сколько игроков,
  начавших участие в событии, продолжили играть
  в течение определенного периода после его завершения.
  Высокий уровень удержания свидетельствует о том, что событие было 
  привлекательным для игроков.
* **Conversion Rate**.  Эта метрика отражает процент игроков,
  которые завершили все требуемые уровни события и получили награду.
  Высокий Conversion Rate говорит о том, что событие было достаточно
  привлекательным и выполнимым для игроков.
* **Средняя продолжительность игровой сессии**.С помощью этой метрики 
  мы можем оценить,сколько времени игроки стали проводить в игре в период данного события.
* **Оценка удовлетворенности клиентов (customer satisfaction score, CSAT) конкретнго по этому событию**.
  Эта метрика позволяет измерить общий уровень недовольства пользователя по поводу игрового события.
* **Отзывы и обратная связь игроков**. Позитивные отзывы могут указывать на успешные аспекты события,
  а негативные - на его недостатки и области для улучшения.

### Ответ на второй вопрос:

Все метрики, описанные выше остануться, однако, на мой взгляд, потребуются еще как минимум 3 важные метрики: 
* **Среднее количество попыток на уровень.** Эта метрика отразит, сколько попыток требуется в среднем игрокам для прохождения каждого уровня в усложненной механике. Большое количество попыток может свидетельствовать о высокой сложности события в игре.
* **Среднее количество откатов назад.** Эта метрика позволит оценить, насколько часто игрокам приходится откатываться назад из-за неудачных попыток. Большое количество откатов может указывать на недостаточно сбалансированную сложность игры.
* **Среднее время прохождения события.** Оценка времени, затраченного игроками на прохождение события, может помочь понять, как усложнение механики влияет на общую продолжительность участия в событии.